# News Modeling

Topic modeling involves **extracting features from document terms** and using
mathematical structures and frameworks like matrix factorization and SVD to generate **clusters or groups of terms** that are distinguishable from each other and these clusters of words form topics or concepts

Topic modeling is a method for **unsupervised classification** of documents, similar to clustering on numeric data

These concepts can be used to interpret the main **themes** of a corpus and also make **semantic connections among words that co-occur together** frequently in various documents

Topic modeling can help in the following areas:
- discovering the **hidden themes** in the collection
- **classifying** the documents into the discovered themes
- using the classification to **organize/summarize/search** the documents

Frameworks and algorithms to build topic models:
- Latent semantic indexing
- Latent Dirichlet allocation
- Non-negative matrix factorization

## Latent Dirichlet Allocation (LDA)
The latent Dirichlet allocation (LDA) technique is a **generative probabilistic model** where each **document is assumed to have a combination of topics** similar to a probabilistic latent semantic indexing model

In simple words, the idea behind LDA is that of two folds:
- each **document** can be described by a **distribution of topics**
- each **topic** can be described by a **distribution of words**

### LDA Algorithm

- 1. For each document, **randomly initialize each word to one of the K topics** (k is chosen beforehand)
- 2. For each document D, go through each word w and compute:
    - **P(T |D)** , which is a proportion of words in D assigned to topic T
    - **P(W |T )** , which is a proportion of assignments to topic T over all documents having the word W
- **Reassign word W with topic T** with probability P(T |D)´ P(W |T ) considering all other words and their topic assignments

![LDA](https://raw.githubusercontent.com/subashgandyer/datasets/main/images/LDA.png)

### Steps
- Install the necessary library
- Import the necessary libraries
- Download the dataset
- Load the dataset
- Pre-process the dataset
    - Stop words removal
    - Email removal
    - Non-alphabetic words removal
    - Tokenize
    - Lowercase
    - BiGrams & TriGrams
    - Lemmatization
- Create a dictionary for the document
- Filter low frequency words
- Create an Index to word dictionary
- Train the Topic Model
- Predict on the dataset
- Evaluate the Topic Model
    - Model Perplexity
    - Topic Coherence
- Visualize the topics

### Install the necessary library

In [60]:
#! pip install pyLDAvis gensim spacy

### Import the libraries

In [61]:
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from gensim.models import LdaModel
from gensim.corpora import Dictionary
from pprint import pprint
import pandas as pd
from nltk.tokenize import RegexpTokenizer
from nltk.stem.wordnet import WordNetLemmatizer
from gensim import corpora, models
import gensim

In [62]:
nltk.download('stopwords')

[nltk_data] Error loading stopwords: <urlopen error [SSL:
[nltk_data]     CERTIFICATE_VERIFY_FAILED] certificate verify failed:
[nltk_data]     unable to get local issuer certificate (_ssl.c:997)>


False

### Download the dataset
Dataset: https://raw.githubusercontent.com/subashgandyer/datasets/main/newsgroups.json

#### 20-Newsgroups dataset
- 11K newsgroups posts
- 20 news topics

In [63]:
! wget https://raw.githubusercontent.com/subashgandyer/datasets/main/newsgroups.json

--2022-11-13 08:20:35--  https://raw.githubusercontent.com/subashgandyer/datasets/main/newsgroups.json
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.110.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 23237087 (22M) [text/plain]
Saving to: ‘newsgroups.json.3’

newsgroups.json.3   100%[===================>]  22.16M  7.03MB/s    in 3.2s    

2022-11-13 08:20:39 (7.03 MB/s) - ‘newsgroups.json.3’ saved [23237087/23237087]



### Load the dataset

In [64]:
import json

In [65]:
path = "newsgroups.json"

In [66]:
with open(path, "r") as json_file:
    data = json.load(json_file)

In [67]:
data

{'content': {'0': "From: lerxst@wam.umd.edu (where's my thing)\nSubject: WHAT car is this!?\nNntp-Posting-Host: rac3.wam.umd.edu\nOrganization: University of Maryland, College Park\nLines: 15\n\n I was wondering if anyone out there could enlighten me on this car I saw\nthe other day. It was a 2-door sports car, looked to be from the late 60s/\nearly 70s. It was called a Bricklin. The doors were really small. In addition,\nthe front bumper was separate from the rest of the body. This is \nall I know. If anyone can tellme a model name, engine specs, years\nof production, where this car is made, history, or whatever info you\nhave on this funky looking car, please e-mail.\n\nThanks,\n- IL\n   ---- brought to you by your neighborhood Lerxst ----\n\n\n\n\n",
  '1': "From: guykuo@carson.u.washington.edu (Guy Kuo)\nSubject: SI Clock Poll - Final Call\nSummary: Final call for SI clock reports\nKeywords: SI,acceleration,clock,upgrade\nArticle-I.D.: shelley.1qvfo9INNc3s\nOrganization: University

In [68]:
len(data)

3

In [69]:
data.keys()

dict_keys(['content', 'target', 'target_names'])

In [70]:
data['content']

{'0': "From: lerxst@wam.umd.edu (where's my thing)\nSubject: WHAT car is this!?\nNntp-Posting-Host: rac3.wam.umd.edu\nOrganization: University of Maryland, College Park\nLines: 15\n\n I was wondering if anyone out there could enlighten me on this car I saw\nthe other day. It was a 2-door sports car, looked to be from the late 60s/\nearly 70s. It was called a Bricklin. The doors were really small. In addition,\nthe front bumper was separate from the rest of the body. This is \nall I know. If anyone can tellme a model name, engine specs, years\nof production, where this car is made, history, or whatever info you\nhave on this funky looking car, please e-mail.\n\nThanks,\n- IL\n   ---- brought to you by your neighborhood Lerxst ----\n\n\n\n\n",
 '1': "From: guykuo@carson.u.washington.edu (Guy Kuo)\nSubject: SI Clock Poll - Final Call\nSummary: Final call for SI clock reports\nKeywords: SI,acceleration,clock,upgrade\nArticle-I.D.: shelley.1qvfo9INNc3s\nOrganization: University of Washingto

In [71]:
len(data['content'])

11314

In [72]:
data['content']['0']

"From: lerxst@wam.umd.edu (where's my thing)\nSubject: WHAT car is this!?\nNntp-Posting-Host: rac3.wam.umd.edu\nOrganization: University of Maryland, College Park\nLines: 15\n\n I was wondering if anyone out there could enlighten me on this car I saw\nthe other day. It was a 2-door sports car, looked to be from the late 60s/\nearly 70s. It was called a Bricklin. The doors were really small. In addition,\nthe front bumper was separate from the rest of the body. This is \nall I know. If anyone can tellme a model name, engine specs, years\nof production, where this car is made, history, or whatever info you\nhave on this funky looking car, please e-mail.\n\nThanks,\n- IL\n   ---- brought to you by your neighborhood Lerxst ----\n\n\n\n\n"

In [73]:
data_dict=data['content']

In [74]:
type(data_dict)

dict

In [75]:
df = pd.DataFrame(data_dict.values(), columns=['Description'])

In [76]:
df

Description
0      From: lerxst@wam.umd.edu (where's my thing)\nS...
1      From: guykuo@carson.u.washington.edu (Guy Kuo)...
2      From: twillis@ec.ecn.purdue.edu (Thomas E Will...
3      From: jgreen@amber (Joe Green)\nSubject: Re: W...
4      From: jcm@head-cfa.harvard.edu (Jonathan McDow...
...                                                  ...
11309  From: jim.zisfein@factory.com (Jim Zisfein) \n...
11310  From: ebodin@pearl.tufts.edu\nSubject: Screen ...
11311  From: westes@netcom.com (Will Estes)\nSubject:...
11312  From: steve@hcrlgw (Steven Collins)\nSubject: ...
11313  From: gunning@cco.caltech.edu (Kevin J. Gunnin...

[11314 rows x 1 columns]

### Preprocess the data

### Email Removal

In [77]:
df

Description
0      From: lerxst@wam.umd.edu (where's my thing)\nS...
1      From: guykuo@carson.u.washington.edu (Guy Kuo)...
2      From: twillis@ec.ecn.purdue.edu (Thomas E Will...
3      From: jgreen@amber (Joe Green)\nSubject: Re: W...
4      From: jcm@head-cfa.harvard.edu (Jonathan McDow...
...                                                  ...
11309  From: jim.zisfein@factory.com (Jim Zisfein) \n...
11310  From: ebodin@pearl.tufts.edu\nSubject: Screen ...
11311  From: westes@netcom.com (Will Estes)\nSubject:...
11312  From: steve@hcrlgw (Steven Collins)\nSubject: ...
11313  From: gunning@cco.caltech.edu (Kevin J. Gunnin...

[11314 rows x 1 columns]

In [78]:
import re

In [79]:
df['Description'] = df['Description'].apply(lambda x: re.sub(r'([a-zA-Z0-9+.-]+@[a-zA-Z0-9+.-]+)', "", x))
df['Description'] = df['Description'].apply(lambda x: re.sub(r'([a-zA-Z0-9+.-]+@[a-zA-Z0-9+.-]+\.[a-zA-Z0-9+.-]+)', "", x))
df['Description'] = df['Description'].apply(lambda x: re.sub(r'([a-zA-Z0-9+.-]+@[a-zA-Z0-9+.-]+\.[a-zA-Z0-9+.-]+\.[a-zA-Z0-9+.-]+)', "", x))
df['Description'] = df['Description'].apply(lambda x: re.sub(r'([a-zA-Z0-9+.-]+@[a-zA-Z0-9+.-]+\.[a-zA-Z0-9+.-]+\.[a-zA-Z0-9+.-]+\.[a-zA-Z0-9+.-]+)', "", x))

In [80]:
df

Description
0      From:  (where's my thing)\nSubject: WHAT car i...
1      From:  (Guy Kuo)\nSubject: SI Clock Poll - Fin...
2      From:  (Thomas E Willis)\nSubject: PB question...
3      From:  (Joe Green)\nSubject: Re: Weitek P9000 ...
4      From:  (Jonathan McDowell)\nSubject: Re: Shutt...
...                                                  ...
11309  From:  (Jim Zisfein) \nSubject: Re: Migraines ...
11310  From: \nSubject: Screen Death: Mac Plus/512\nL...
11311  From:  (Will Estes)\nSubject: Mounting CPU Coo...
11312  From:  (Steven Collins)\nSubject: Re: Sphere f...
11313  From:  (Kevin J. Gunning)\nSubject: stolen CBR...

[11314 rows x 1 columns]

### Newline Removal

In [81]:
temp = []
for i in df['Description']:
    i = i.replace('\n', ' ')
    temp.append(i)
df['Description'] = temp

In [82]:
df

Description
0      From:  (where's my thing) Subject: WHAT car is...
1      From:  (Guy Kuo) Subject: SI Clock Poll - Fina...
2      From:  (Thomas E Willis) Subject: PB questions...
3      From:  (Joe Green) Subject: Re: Weitek P9000 ?...
4      From:  (Jonathan McDowell) Subject: Re: Shuttl...
...                                                  ...
11309  From:  (Jim Zisfein)  Subject: Re: Migraines a...
11310  From:  Subject: Screen Death: Mac Plus/512 Lin...
11311  From:  (Will Estes) Subject: Mounting CPU Cool...
11312  From:  (Steven Collins) Subject: Re: Sphere fr...
11313  From:  (Kevin J. Gunning) Subject: stolen CBR9...

[11314 rows x 1 columns]

### Single Quotes Removal

In [83]:
# Remove single quote
# Lower case
temp = []
for i in df['Description']:
    i = i.replace("'", ' ')
    i = i.lower()
    temp.append(i)
df['Description'] = temp

In [84]:
df.head(10)

Description
0  from:  (where s my thing) subject: what car is...
1  from:  (guy kuo) subject: si clock poll - fina...
2  from:  (thomas e willis) subject: pb questions...
3  from:  (joe green) subject: re: weitek p9000 ?...
4  from:  (jonathan mcdowell) subject: re: shuttl...
5  from:  (foxvog douglas) subject: re: rewording...
6  from:  (brian manning delaney) subject: brain ...
7  from:  (grubb) subject: re: ide vs scsi organi...
8  from:  subject: win 3.0 icon help please! orga...
9  from:  (stan kerr) subject: re: sigma designs ...

In [85]:
list_doc = list(df['Description'])

In [86]:
list_doc[4]

'from:  (jonathan mcdowell) subject: re: shuttle launch question organization: smithsonian astrophysical observatory, cambridge, ma,  usa distribution: sci lines: 23  from article <>, by  (tom a baker): >>in article <>,  (pack rat) writes... >>>"clear caution & warning memory.  verify no unexpected >>>errors. ...".  i am wondering what an "expected error" might >>>be.  sorry if this is a really dumb question, but >  > parity errors in memory or previously known conditions that were waivered. >    "yes that is an error, but we already knew about it" > i d be curious as to what the real meaning of the quote is. >  > tom   my understanding is that the  expected errors  are basically known bugs in the warning system software - things are checked that don t have the right values in yet because they aren t set till after launch, and suchlike. rather than fix the code and possibly introduce new bugs, they just tell the crew  ok, if you see a warning no. 213 before liftoff, ignore it .   - jon

### Tokenize
- Create **sent_to_words()** 
    - Use **gensim.utils.simple_preprocess**
    - Use **generator** instead of an usual function

In [87]:
def sent_to_words(list_doc):
    return [gensim.utils.simple_preprocess(doc) for doc in list_doc]

In [88]:
list_of_doc_tok = sent_to_words(list_doc)

In [89]:
list_of_doc_tok[4]

['from',
 'jonathan',
 'mcdowell',
 'subject',
 're',
 'shuttle',
 'launch',
 'question',
 'organization',
 'smithsonian',
 'astrophysical',
 'observatory',
 'cambridge',
 'ma',
 'usa',
 'distribution',
 'sci',
 'lines',
 'from',
 'article',
 'by',
 'tom',
 'baker',
 'in',
 'article',
 'pack',
 'rat',
 'writes',
 'clear',
 'caution',
 'warning',
 'memory',
 'verify',
 'no',
 'unexpected',
 'errors',
 'am',
 'wondering',
 'what',
 'an',
 'expected',
 'error',
 'might',
 'be',
 'sorry',
 'if',
 'this',
 'is',
 'really',
 'dumb',
 'question',
 'but',
 'parity',
 'errors',
 'in',
 'memory',
 'or',
 'previously',
 'known',
 'conditions',
 'that',
 'were',
 'waivered',
 'yes',
 'that',
 'is',
 'an',
 'error',
 'but',
 'we',
 'already',
 'knew',
 'about',
 'it',
 'be',
 'curious',
 'as',
 'to',
 'what',
 'the',
 'real',
 'meaning',
 'of',
 'the',
 'quote',
 'is',
 'tom',
 'my',
 'understanding',
 'is',
 'that',
 'the',
 'expected',
 'errors',
 'are',
 'basically',
 'known',
 'bugs',
 'in',
 '

### Stop words Removal
- Extend the stop words corpus with the following words
    - from
    - subject
    - re
    - edu
    - use

In [90]:
stops = set(stopwords.words('english'))

In [91]:
for i in ['from', 'subject', 're', 'edu', 'use']:
    stops.add(i)

In [92]:
for i in ['from', 'subject', 're', 'edu', 'use']:
    if i in stops:
        print(f"{i} is in the stop word list")

from is in the stop word list
subject is in the stop word list
re is in the stop word list
edu is in the stop word list
use is in the stop word list


#### remove_stopwords( )

In [93]:
# remove stopwords and non-alphabetic words
def remove_stopwords(list_of_doc_tok):
    output = []
    for i in range(len(list_of_doc_tok)):
        one_doc = [token for token in list_of_doc_tok[i] if token not in stops and token.isalpha()]
        output.append(one_doc)
    return output

In [94]:
list_of_doc_tok_NoStopWord = remove_stopwords(list_of_doc_tok)

### Bigrams
- Use **gensim.models.Phrases**
- 100 as threshold

In [95]:
from gensim.models import Phrases
from gensim.models.phrases import Phraser

#### make_bigrams( )

In [96]:
def make_bigrams(text):
    bigrams_phrases = Phrases(text, min_count=5, threshold=100)
    bigram = Phraser(bigrams_phrases)
    return [bigram[doc] for doc in text]

In [97]:
list_of_doc_tok_NoStopWord_bi = make_bigrams(list_of_doc_tok_NoStopWord)

In [98]:
len(list_of_doc_tok_NoStopWord_bi)

11314

In [99]:
len(list_of_doc_tok_NoStopWord_bi[0])

58

### Lemmatization
- Use spacy
    - Download spacy en model (if you have not done that before)
    - Load the spacy model

In [100]:
import spacy

In [101]:
! python3 -m spacy download en

⚠ As of spaCy v3.0, shortcuts like 'en' are deprecated. Please use the
full pipeline package name 'en_core_web_sm' instead.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 7.3 MB/s eta 0:00:0000:0100:01m
--- Logging error ---
Traceback (most recent call last):
  File "/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/pip/_internal/utils/logging.py", line 177, in emit
    self.console.print(renderable, overflow="ignore", crop=False, style=style)
  File "/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/pip/_vendor/rich/console.py", line 1673, in print
    extend(render(renderable, render_options))
  File "/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/pip/_vendor/rich/console.py", line 1305, in render
    for render_output in iter_render:
  File "/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/pip/_internal/utils/logging.py", line 134, in __rich_console

In [102]:
nlp = spacy.load('en_core_web_sm', disable=['parser', 'ner'])

#### lemmatizaton( )

In [103]:
def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

In [104]:
def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

In [105]:
data_lemmatized = lemmatization(list_of_doc_tok_NoStopWord_bi, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV'])

In [106]:
print(data_lemmatized[0])

['thing', 'car', 'nntp_poste', 'host', 'park', 'line', 'wonder', 'enlighten', 'car', 'see', 'day', 'door', 'sport', 'car', 'look', 'late', 'early', 'call', 'door', 'really', 'small', 'addition', 'separate', 'rest', 'body', 'know', 'tellme', 'model', 'name', 'engine', 'spec', 'year', 'production', 'car', 'make', 'history', 'info', 'funky', 'look', 'car', 'mail', 'thank', 'bring', 'neighborhood', 'lerxst']


### Create a Dictionary

In [107]:
dictionary = Dictionary(data_lemmatized)

### Create Corpus

### Filter low-frequency words

In [108]:
dictionary.filter_extremes(no_below=10, no_above=0.5)
# convert tokenized documents into a document-term matrix
# In each document, what terms does it contain? and how many?
corpus = [dictionary.doc2bow(text) for text in data_lemmatized]

### Create Index 2 word dictionary

In [109]:
dictionary

In [110]:
temp = dictionary[0] # This is only to "load" the dictionary.
id2word = dictionary.id2token

In [111]:
id2word

{0: 'addition',
 1: 'body',
 2: 'bring',
 3: 'call',
 4: 'car',
 5: 'day',
 6: 'door',
 7: 'early',
 8: 'engine',
 9: 'enlighten',
 10: 'history',
 11: 'host',
 12: 'info',
 13: 'know',
 14: 'late',
 15: 'look',
 16: 'mail',
 17: 'make',
 18: 'model',
 19: 'name',
 20: 'neighborhood',
 21: 'nntp_poste',
 22: 'park',
 23: 'production',
 24: 'really',
 25: 'rest',
 26: 'see',
 27: 'separate',
 28: 'small',
 29: 'spec',
 30: 'sport',
 31: 'thank',
 32: 'thing',
 33: 'wonder',
 34: 'year',
 35: 'acceleration',
 36: 'adapter',
 37: 'add',
 38: 'answer',
 39: 'attain',
 40: 'base',
 41: 'brave',
 42: 'brief',
 43: 'card',
 44: 'clock',
 45: 'cpu',
 46: 'detail',
 47: 'do',
 48: 'especially',
 49: 'experience',
 50: 'fair',
 51: 'final',
 52: 'floppy',
 53: 'floppy_disk',
 54: 'functionality',
 55: 'heat_sink',
 56: 'hour',
 57: 'keyword',
 58: 'knowledge',
 59: 'message',
 60: 'network',
 61: 'next',
 62: 'number',
 63: 'oscillator',
 64: 'please',
 65: 'poll',
 66: 'procedure',
 67: 'rate',

### Build a News Topic Model

#### LdaModel
- **num_topics** : this is the number of topics you need to define beforehand
- **chunksize** : the number of documents to be used in each training chunk
- **alpha** : this is the hyperparameters that affect the sparsity of the topics
- **passess** : total number of training assess

In [112]:
ldamodel = LdaModel(corpus, num_topics=20, id2word = id2word, passes=20, alpha=0.01, chunksize=1500)

### Print the Keyword in the 10 topics

In [113]:
for idx in range(20):
    print("Topic #%s:" % idx, ldamodel.print_topic(idx, 10))

Topic #0: 0.027*"value" + 0.021*"system" + 0.016*"point" + 0.015*"nntp_poste" + 0.013*"article" + 0.012*"moral" + 0.010*"think" + 0.010*"morality" + 0.010*"objective" + 0.009*"define"
Topic #1: 0.057*"nntp_poste" + 0.051*"host" + 0.030*"post" + 0.030*"article" + 0.029*"thank" + 0.026*"know" + 0.026*"mail" + 0.023*"reply" + 0.019*"question" + 0.017*"help"
Topic #2: 0.038*"problem" + 0.020*"work" + 0.016*"get" + 0.016*"time" + 0.012*"try" + 0.012*"article" + 0.009*"know" + 0.009*"system" + 0.009*"go" + 0.008*"take"
Topic #3: 0.018*"wire" + 0.013*"use" + 0.013*"circuit" + 0.011*"lead" + 0.011*"get" + 0.010*"current" + 0.010*"low" + 0.009*"ground" + 0.009*"article" + 0.008*"power"
Topic #4: 0.046*"window" + 0.021*"use" + 0.018*"do" + 0.017*"display" + 0.017*"run" + 0.016*"color" + 0.014*"program" + 0.014*"get" + 0.012*"application" + 0.012*"screen"
Topic #5: 0.019*"drive" + 0.018*"card" + 0.013*"system" + 0.011*"get" + 0.011*"driver" + 0.010*"nntp_poste" + 0.010*"use" + 0.010*"scsi" + 0.00

## Evaluation of Topic Models
- Model Perplexity
- Topic Coherence

### Model Perplexity

Model perplexity is a measurement of **how well** a **probability distribution** or probability model **predicts a sample**

In [114]:
perplexity = ldamodel.log_perplexity(corpus) # a measure of how good the model is. lower the better.
print('\nlog_perplexity: ', perplexity)


log_perplexity:  -7.34876142313764


### Topic Coherence
Topic Coherence measures score a single topic by measuring the **degree of semantic similarity** between **high scoring words** in the topic.

In [115]:
from gensim.models import CoherenceModel
# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=ldamodel, texts=data_lemmatized, dictionary=dictionary, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Coherence Score:  0.557517810793899


### Visualize the Topic Model
- Use **pyLDAvis**
    - designed to help users **interpret the topics** in a topic model that has been fit to a corpus of text data
    - extracts information from a fitted LDA topic model to inform an interactive web-based visualization

In [116]:
# Visualization
import pyLDAvis.gensim_models

In [117]:
pyLDAvis.enable_notebook()

In [118]:
pyLDAvis.gensim_models.prepare(ldamodel, corpus, dictionary)

/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  by='saliency', ascending=False).head(R).drop('saliency', 1)
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib and slated for removal in Python 3.12; see the module's documentation for alternative uses
  from imp import reload
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib and slated for removal in Python 3.12; see the module's documentation for alternative uses
  from imp import reload
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/past/builtins/misc.py:45: Deprec

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
15     0.109210  0.074935       1        1  16.344533
12     0.138322 -0.039947       2        1  13.242913
16     0.020948  0.007195       3        1   7.126795
10     0.003782  0.249156       4        1   6.668164
14     0.121652 -0.057401       5        1   6.062957
5      0.074320 -0.132695       6        1   5.919313
11    -0.468822 -0.120569       7        1   5.755936
8      0.091507 -0.022035       8        1   5.670217
7      0.008381  0.162085       9        1   5.559794
2      0.114556 -0.081895      10        1   4.195685
4      0.092013 -0.127683      11        1   4.043138
19     0.074109  0.090274      12        1   4.030736
1      0.008604 -0.161198      13        1   2.770219
17    -0.007723  0.158621      14        1   2.199722
13    -0.067115 -0.003903      15        1   2.146310
3      0.047444 -0.086847      16        1   2.049847
9     -0.039457  0.163103      17        1   2.037853
6     -0.052983 -0.039744      18        1   1.858959
0      0.017898 -0.087178      19        1   1.667003
18    -0.286645  0.055725      20        1   0.649907, topic_info=            Term          Freq         Total Category  logprob  loglift
3190          ax  61257.000000  61257.000000  Default  30.0000  30.0000
21    nntp_poste   4858.000000   4858.000000  Default  29.0000  29.0000
975       window   2059.000000   2059.000000  Default  28.0000  28.0000
11          host   3801.000000   3801.000000  Default  27.0000  27.0000
165      article   7341.000000   7341.000000  Default  26.0000  26.0000
...          ...           ...           ...      ...      ...      ...
419        brown     44.665479    102.878340  Topic20  -5.0712   4.2017
4036   vancouver     44.381877    109.643260  Topic20  -5.0776   4.1317
1053        none     45.455246    335.631522  Topic20  -5.0537   3.0368
4309       drink     43.587161    171.374185  Topic20  -5.0956   3.6670
1687        rich     43.024354    173.075724  Topic20  -5.1086   3.6441

[1363 rows x 6 columns], token_table=      Topic      Freq         Term
term                              
5886      8  0.982385          aaa
433       1  0.946197     absolute
433      12  0.011132     absolute
433      19  0.038961     absolute
3839      6  0.945848  accelerator
...     ...       ...          ...
34       19  0.017033         year
5502     20  0.969801      zionism
2056      4  0.345235         zone
2056      8  0.189057         zone
2056     20  0.460313         zone

[3911 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[16, 13, 17, 11, 15, 6, 12, 9, 8, 3, 5, 20, 2, 18, 14, 4, 10, 7, 1, 19])